In [54]:
import time

def timeit(func, *args, **kwargs):
    start = time.time()
    result = func(*args, **kwargs)
    end = time.time()
    print(f"Time taken by {func.__name__}: {end - start} seconds")
    return time.time() - start, result

In [55]:
from stripsProblem import *
from searchMPP import *
from stripsForwardPlanner import *
from searchGeneric import Searcher

blocks1dom = create_blocks_world({'a','b','c', 'd'}) # 'd', 'e'
blocks1 = Planning_problem(blocks1dom,
     {on('a'):'table', clear('a'):False,
      on('b'):'c',  clear('b'):True,
      on('c'):'table', clear('c'):False,
      on('d'):'a', clear('d'): True,
      # on('e'): 'd', clear('e'): True,
      }, # initial state
     {
     #     on('d'): 'e', on('b') : 'd', 
         on('d'):'c', on('c'):'b', on('b'):'a' })  #goal
print("=" * 160)
time1, result = timeit(lambda: AStarSearcher(Forward_STRIPS(blocks1)).search())

4 Expanding: {'a_is_on': 'table', 'clear_a': False, 'b_is_on': 'c', 'clear_b': True, 'c_is_on': 'table', 'clear_c': False, 'd_is_on': 'a', 'clear_d': True} (cost: 0)
2 Expanding: {'a_is_on': 'table', 'clear_a': False, 'b_is_on': 'c', 'clear_b': True, 'c_is_on': 'table', 'clear_c': False, 'd_is_on': 'a', 'clear_d': True} with neighbors [{'a_is_on': 'table', 'clear_a': False, 'b_is_on': 'c', 'clear_b': True, 'c_is_on': 'table', 'clear_c': False, 'd_is_on': 'a', 'clear_d': True} --move_b_from_c_to_table--> {'a_is_on': 'table', 'clear_a': False, 'b_is_on': 'table', 'clear_b': True, 'c_is_on': 'table', 'clear_c': True, 'd_is_on': 'a', 'clear_d': True}, {'a_is_on': 'table', 'clear_a': False, 'b_is_on': 'c', 'clear_b': True, 'c_is_on': 'table', 'clear_c': False, 'd_is_on': 'a', 'clear_d': True} --move_d_from_a_to_table--> {'a_is_on': 'table', 'clear_a': True, 'b_is_on': 'c', 'clear_b': True, 'c_is_on': 'table', 'clear_c': False, 'd_is_on': 'table', 'clear_d': True}, {'a_is_on': 'table', 'clea

In [56]:
from copy import deepcopy
from typing import Dict, List
from stripsProblem import Planning_problem

class BlocksWorldNaiveHeuristic():

    def __init__(self, problem: Planning_problem) -> None:
        self.expected_columns = self._calculate_columns(problem.goal)
        self.expected_fundaments = self._calculate_fundaments(problem.goal)


    def _calculate_columns(self, goal) -> Dict[str, int]:
        unique_blocks = set()
        for k, v in goal.items():
            if v != 'table':
                unique_blocks.add(v) 
            if k[0] != 'table':
                unique_blocks.add(k[0])
       

        goal = {k[0]: v for k, v in goal.items()}

        result = dict()
        for block in unique_blocks:
            curr = block
            deepness = 0

            while curr in goal and goal[curr] != 'table':
                curr = goal[curr]
                deepness += 1

            result[block] = deepness

        return result
        # TODO:
        # return a dict of form:
        # { <block name> : <index of column in the goal state> }


    def _calculate_fundaments(self, goal) -> Dict[str, List[str]]:
        # TODO:
        # return a dict of form:
        # { <block name> : <list of the blocks below it in the goal state> }
        unique_blocks = set()
        for k, v in goal.items():
            if v != 'table':
                unique_blocks.add(v) 
            if k[0] != 'table':
                unique_blocks.add(k[0])   

        goal = {k[0]: v for k, v in goal.items()}

        result = dict()
        for block in unique_blocks:
            curr = block
            temp = list()

            while curr in goal and goal[curr] != 'table':
                curr = goal[curr]
                temp.append(curr)

            result[block] = temp

        return result

    def __call__(self, state, *args) -> int:
        
        temp = {k : v for k, v in state.items() if not k.startswith('clear') }
        state_columns = self._calculate_columns(temp)
        state_fundaments = self._calculate_fundaments(temp)

        result = 0
        checked = list()

        for element, expectedColumn in self.expected_columns.items():
            if element not in state_columns:
                print(state)
                print(state_columns)


            if expectedColumn != state_columns[element]:
                result += 1
                checked.append(element)

        for element, expectedFundaments in self.expected_fundaments.items():
            if element in checked:
                continue

            for i in range(len(expectedFundaments)):
                if expectedFundaments[i] != state_fundaments[element][i]:
                    result += 2

        return result
        # TODO:
        # - add `1` to the heuristic value per each block placed in an incorrect column
        # - for other blocks, add `2` if their fundament is incorrect 
        # tip. use self.expected_columns and self.expected_fundaments


heur = BlocksWorldNaiveHeuristic(blocks1)

time2, result = timeit(lambda: AStarSearcher(Forward_STRIPS(blocks1, heur)).search())

4 Expanding: {'a_is_on': 'table', 'clear_a': False, 'b_is_on': 'c', 'clear_b': True, 'c_is_on': 'table', 'clear_c': False, 'd_is_on': 'a', 'clear_d': True} (cost: 0)
2 Expanding: {'a_is_on': 'table', 'clear_a': False, 'b_is_on': 'c', 'clear_b': True, 'c_is_on': 'table', 'clear_c': False, 'd_is_on': 'a', 'clear_d': True} with neighbors [{'a_is_on': 'table', 'clear_a': False, 'b_is_on': 'c', 'clear_b': True, 'c_is_on': 'table', 'clear_c': False, 'd_is_on': 'a', 'clear_d': True} --move_b_from_c_to_table--> {'a_is_on': 'table', 'clear_a': False, 'b_is_on': 'table', 'clear_b': True, 'c_is_on': 'table', 'clear_c': True, 'd_is_on': 'a', 'clear_d': True}, {'a_is_on': 'table', 'clear_a': False, 'b_is_on': 'c', 'clear_b': True, 'c_is_on': 'table', 'clear_c': False, 'd_is_on': 'a', 'clear_d': True} --move_d_from_a_to_table--> {'a_is_on': 'table', 'clear_a': True, 'b_is_on': 'c', 'clear_b': True, 'c_is_on': 'table', 'clear_c': False, 'd_is_on': 'table', 'clear_d': True}, {'a_is_on': 'table', 'clea

In [59]:
print(f"Searching with naive heuristic is {time1/time2:.2f} times faster than without heuristic")

Searching with naive heuristic is 33.91 times faster than without heuristic
